In [1]:
import numpy as np
import matplotlib.pyplot as plt
import os
import time
import torch
import torch.nn as nn
import torch.optim as optim
import torch.nn.functional as F
import torch.optim.lr_scheduler as lr_scheduler
import math
import random

MIN_LIST_LEN = 16
MAX_LIST_LEN = 16
MAX_STEPS = 640

SUCCESS_REWARD = 0.5
STEP_REWARD = -0.3
COMPARISON_ENTROPY_MULTIPLIER = -0.00
SWAP_REWARD = 1.0
INVALID_ACTION_REWARD = -10.0
LONGTERM_GAMMA = 0.99
SHORTTERM_GAMMA = 0.7

EPS_START = 0.5
EPS_END = 0.1
EPS_DECAY = 1000
LR_SCHEDULER_GAMMA = 0.9
NUM_EPISODES = 3999
EPISODES_SAVE = 1000
OUTPUT_DIR = '/home/mcwave/code/autocode/datasets/rl_sort_transformer_easy/list16_transformer4_192_gamma07_step640_v3_data2'

# Define the vocabulary
# Define the vocabulary
vocab = {
    'Comparison': 0,
    'Swap': 1,
    'less': 2,
    'equal': 3,
    'more': 4,
    '0': 5,
    '1': 6,
    '2': 7,
    '3': 8,
    '4': 9,
    '5': 10,
    '6': 11,
    '7': 12,
    '8': 13,
    '9': 14,
    '10': 15,
    '11': 16,
    '12': 17,
    '13': 18,
    '14': 19,
    '15': 20,
    'len1': 21,
    'len2': 22,
    'len3': 23,
    'len4': 24,
    'len5': 25,
    'len6': 26,
    'len7': 27,
    'len8': 28,
    'len9': 29,
    'len10': 30,
    'len11': 31,
    'len12': 32,
    'len13': 33,
    'len14': 34,
    'len15': 35,
    'len16': 36,
    'pos0': 37,
    'pos1': 38,
    'pos2': 39,
    'pos3': 40,
    'pos4': 41,
    'pos5': 42,
    'pos6': 43,
    'pos7': 44,
    'pos8': 45,
    'pos9': 46,
    'pos10': 47,
    'pos11': 48,
    'pos12': 49,
    'pos13': 50,
    'pos14': 51,
    'pos15': 52,
}
inv_vocab = {v: k for k, v in vocab.items()}

def compute_entropy(N, alpha=1):
    K = 2**N
    values = np.arange(K)
    unnormalized_probs = np.exp(-alpha * values)
    Z = unnormalized_probs.sum()
    probs = unnormalized_probs / Z
    return values, -np.log2(probs)

_, int_entropy = compute_entropy(4)

def get_entropy_of_integer(x):
    x = min(15, abs(x))
    return int_entropy[x]

def compute_min_delta_entropy(comparisons):
    # Initialize the result list to store minDelta values
    min_delta = None

    # Iterate through each pair in the comparisons list
    i = len(comparisons) - 1
    xi, yi = comparisons[i]
    if i == 0:
        # For i = 0, use the first case directly
        min_delta = (xi, min(yi, yi - xi), 0)
    else:
        # For i > 0, compute all possible options and select the minimal one
        options = []

        # Simple Entropy
        simple_entropy = (xi, min(yi, yi - xi), 0)
        options.append(simple_entropy)

        # First Delta Entropy
        xi_prev, yi_prev = comparisons[i - 1]
        first_delta_entropy = (xi - xi_prev, yi - yi_prev, 0)
        options.append(first_delta_entropy)

        # Second Delta Entropy (only valid for i > 1)
        if i > 1:
            xi_prev2, yi_prev2 = comparisons[i - 2]
            second_delta_entropy = (
                (xi - xi_prev) - (xi_prev - xi_prev2),
                (yi - yi_prev) - (yi_prev - yi_prev2),
                0,
            )
            options.append(second_delta_entropy)

        # Arbitrary Position Entropy (only valid for i > 1)
        for j in range(i):
            xj, yj = comparisons[j]
            arbitrary_position_entropy = (
                xi - xj,
                yi - yj,
                min(j, i - j),
            )
            options.append(arbitrary_position_entropy)

        # Find the option with the minimal sum
        min_delta = min(options, key=lambda t: sum([get_entropy_of_integer(x) for x in t]))

    entropy = sum([get_entropy_of_integer(x) for x in min_delta])
    if len(comparisons) == 1:
        return 3 * entropy
    else:
        return entropy

def generate_unique_random_list(length, min_value=1, max_value=100):
    """
    Generates a list of unique random integers within a specified range.
    If duplicates are detected, the list is regenerated.
    
    Args:
        length (int): The length of the list to generate.
        min_value (int): The minimum possible value (inclusive).
        max_value (int): The maximum possible value (inclusive).
        
    Returns:
        list: A list of unique random integers.
    """
    if length > (max_value - min_value + 1):
        raise ValueError("Length exceeds the range of unique values available.")
    
    while True:
        random_list = [random.randint(min_value, max_value) for _ in range(length)]
        if len(set(random_list)) == length:
            return random_list
    
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

# Define the environment
class SortingEnv:
    def __init__(self):
        self.max_steps = MAX_STEPS

    def reset(self):
        self.length = random.randint(MIN_LIST_LEN, MAX_LIST_LEN)
        self.list = generate_unique_random_list(self.length)
        self.sorted_list = sorted(self.list)
        self.indices = None
        self.current_step = 0
        self.done = False
        initial_token = 'len{}'.format(self.length)
        return vocab[initial_token], self.list.copy()
    
    def get_list(self):
        return self.list
    
    def get_list_len(self):
        return len(self.list)

    def step(self, action_tokens):
        action = action_tokens[0]
        reward = -0.01  # default penalty
        response_token = None
        additional_response_tokens = []

        if action == vocab['Comparison']:
            if len(action_tokens) != 3:
                reward = INVALID_ACTION_REWARD
                self.done = True
                return response_token, reward, self.done, self.list.copy()
            index1 = action_tokens[1] - vocab['0']
            index2 = action_tokens[2] - vocab['0']
            if index1 >= self.length or index2 >= self.length or index1 < 0 or index2 < 0:
                reward = INVALID_ACTION_REWARD
                self.done = True
                return response_token, reward, self.done, self.list.copy()
            self.indices = (index1, index2)
            if self.list[index1] < self.list[index2]:
                response_token = vocab['less']
                reward = STEP_REWARD
            elif self.list[index1] == self.list[index2]:
                response_token = vocab['equal']
                reward = STEP_REWARD * 2
            else:
                response_token = vocab['more']
                reward = STEP_REWARD
            final_pos_1 = self.sorted_list.index(self.list[index1])
            final_pos_2 = self.sorted_list.index(self.list[index2])
            additional_response_tokens = [vocab[f"pos{final_pos_1}"], vocab[f"pos{final_pos_2}"]]
        elif action == vocab['Swap']:
            if self.indices is None:
                reward = INVALID_ACTION_REWARD
                self.done = True
                return response_token, reward, self.done, self.list.copy()
            index1, index2 = self.indices
            prev_list = self.list.copy()
            self.list[index1], self.list[index2] = self.list[index2], self.list[index1]
            if self.list == sorted(self.list):
                reward = SUCCESS_REWARD
                self.done = True
            #elif prev_list[index1] > prev_list[index2] and self.list[index1] <= self.list[index2]:
            #    reward = 0.1
            elif (index1 < index2 and prev_list[index1] > prev_list[index2] and self.list[index1] <= self.list[index2]) or \
                (index1 > index2 and prev_list[index1] < prev_list[index2] and self.list[index1] >= self.list[index2]):
                reward = SWAP_REWARD
            elif (index1 < index2 and prev_list[index1] < prev_list[index2] and self.list[index1] >= self.list[index2]) or \
                (index1 > index2 and prev_list[index1] > prev_list[index2] and self.list[index1] <= self.list[index2]):
                reward = -SWAP_REWARD
            else:
                reward = STEP_REWARD
            self.indices = None
        else:
            reward = INVALID_ACTION_REWARD
            self.done = True

        self.current_step += 1
        if self.current_step >= self.max_steps:
            self.done = True
        return response_token, reward, self.done, self.list.copy(), additional_response_tokens


Using device: cuda


In [2]:
# Positional Encoding for Transformer
class PositionalEncoding(nn.Module):
    def __init__(self, d_model, max_len=640):
        super(PositionalEncoding, self).__init__()
        self.dropout = nn.Dropout(p=0.1)

        pe = torch.zeros(max_len, d_model)  # (max_len, d_model)
        position = torch.arange(0, max_len, dtype=torch.float).unsqueeze(1)  # (max_len, 1)
        div_term = torch.exp(torch.arange(0, d_model, 2).float() *
                             (-math.log(10000.0) / d_model))
        pe[:, 0::2] = torch.sin(position * div_term)  # Even indices
        pe[:, 1::2] = torch.cos(position * div_term)  # Odd indices
        pe = pe.unsqueeze(1)  # (max_len, 1, d_model)
        self.register_buffer('pe', pe)

    def forward(self, x):
        x = x + self.pe[:x.size(0)]
        return self.dropout(x)

# Transformer Model
class TransformerModel(nn.Module):
    def __init__(self, vocab_size, d_model=192, nhead=8, num_layers=4):
        super(TransformerModel, self).__init__()
        self.model_type = 'Transformer'
        self.d_model = d_model

        self.embedding = nn.Embedding(vocab_size, d_model)
        self.pos_encoder = PositionalEncoding(d_model)
        encoder_layers = nn.TransformerEncoderLayer(d_model, nhead)
        self.transformer_encoder = nn.TransformerEncoder(encoder_layers, num_layers)
        self.decoder = nn.Linear(d_model, vocab_size)

        self.init_weights()

    def init_weights(self):
        initrange = 0.1
        nn.init.uniform_(self.embedding.weight, -initrange, initrange)
        nn.init.zeros_(self.decoder.bias)
        nn.init.uniform_(self.decoder.weight, -initrange, initrange)

    def forward(self, src):
        src = self.embedding(src) * math.sqrt(self.d_model)
        src = self.pos_encoder(src)
        output = self.transformer_encoder(src)
        output = self.decoder(output)
        return output

def decode(input_tokens, inv_vocab):
    return ' '.join([inv_vocab[x] for x in input_tokens])


def save_checkpoint(model, optimizer, episode, folder, filename):
    """
    Save the model and optimizer state to the designated filepath.

    Args:
        model (nn.Module): The model to save.
        optimizer (torch.optim.Optimizer): The optimizer whose state to save.
        episode (int): The current episode number.
        filepath (str): The path where to save the checkpoint.
    """
    filepath = os.path.join(folder, filename)
    # Ensure the directory exists
    os.makedirs(os.path.dirname(filepath), exist_ok=True)
    # Save the checkpoint
    torch.save({
        'episode': episode,
        'model_state_dict': model.state_dict(),
        'optimizer_state_dict': optimizer.state_dict(),
    }, filepath)
    print(f"Checkpoint saved at episode {episode} to {filepath}")

def load_checkpoint(filepath, model, optimizer):
    """
    Load the model and optimizer state from the designated filepath.

    Args:
        filepath (str): The path from where to load the checkpoint.
        model (nn.Module): The model into which to load the state_dict.
        optimizer (torch.optim.Optimizer): The optimizer into which to load the state.

    Returns:
        int: The episode number to resume from.
    """
    if os.path.isfile(filepath):
        checkpoint = torch.load(filepath, map_location=device)
        model.load_state_dict(checkpoint['model_state_dict'])
        optimizer.load_state_dict(checkpoint['optimizer_state_dict'])
        episode = checkpoint['episode']
        print(f"Checkpoint loaded from {filepath}, resuming from episode {episode}")
        return episode
    else:
        print(f"No checkpoint found at {filepath}, starting from scratch.")
        return 0

In [ ]:
def compute_bellman_returns(raw_rewards, gamma):
    bellman_returns = []
    R = 0
    for r in raw_rewards[::-1]:
        R = r + gamma * R
        bellman_returns.insert(0, R)
    return bellman_returns

# Training Loop
def train(verbose=False):
    # Removed torch.autograd.set_detect_anomaly(True)
    vocab_size = len(vocab)
    model = TransformerModel(vocab_size).to(device)
    optimizer = optim.Adam(model.parameters(), lr=2.3e-5)  # Reduced learning rate
    scheduler = lr_scheduler.ExponentialLR(optimizer, gamma=LR_SCHEDULER_GAMMA)
    
    os.makedirs(OUTPUT_DIR, exist_ok=True)
    f_training_data = open(os.path.join(OUTPUT_DIR, "action_sequence.txt"), "a")
    
    # Optionally, load a checkpoint
    #checkpoint_path = os.path.join('/home/mcwave/code/autocode/datasets/rl_sort_transformer_easy/list16_transformer4_192_gamma07_step640_v3', "ckpt_36000_0.6820_426.26.pth")
    #load_checkpoint(checkpoint_path, model, optimizer)

    episode_cnt = 0
    total_reward = 0.0
    num_successes = 0
    success_step_cnts = []
    
    for episode in range(NUM_EPISODES):
        t1 = time.time()
        model.train()  # Set model to training mode
        env = SortingEnv()
        initial_token_id, current_list = env.reset()
        input_tokens = [initial_token_id]
        output_tokens = [initial_token_id]
        log_probs = []
        rewards = []
        comparisons = []
        steps = 0
        
        state = 'expect_action'
        done = False
        success = False

        while not done and len(input_tokens) < env.max_steps:
            if verbose:
                print(decode(input_tokens, inv_vocab))
                print(env.get_list())
                print(comparisons)
            # Prepare input tensor
            input_seq = torch.tensor(input_tokens, dtype=torch.long, device=device).unsqueeze(1)  # (seq_len, batch_size)
            # Get model output
            with torch.autocast(device_type=device.type, dtype=torch.bfloat16):
                output = model(input_seq)  # (seq_len, batch_size, vocab_size)
                # Get logits for the last token
                logits = output[-1, 0, :]  # (vocab_size)

                # Check for NaNs in logits
                if torch.isnan(logits).any():
                    print(f"Episode {episode}, NaNs in logits before masking.")
                    break

                # Get valid tokens based on state
                def get_valid_tokens(state):
                    action_tokens = [vocab['Comparison'], vocab['Swap']]
                    index_tokens = [vocab[str(i)] for i in range(env.length)]
                    if state == 'expect_action':
                        return action_tokens
                    elif state == 'expect_index1':
                        return index_tokens[:-1]
                    elif state == 'expect_index2':
                        return [x for x in index_tokens if x > input_tokens[-1]]
                    else:
                        # Handle unexpected states by defaulting to expect_action
                        return action_tokens

                valid_token_ids = get_valid_tokens(state)

                # Ensure valid_token_ids are within the vocab range
                if any(idx >= vocab_size or idx < 0 for idx in valid_token_ids):
                    print(f"Episode {episode}, invalid indices in valid_token_ids: {valid_token_ids}")
                    break

                # Mask invalid tokens
                mask_value = -1e9  # Use a large negative value instead of -inf
                mask = torch.full_like(logits, mask_value).to(device)
                mask[valid_token_ids] = 0
                masked_logits = logits + mask

                # Sample action. Have some chance to randomly pick a valid action.
                eps_threshold = EPS_END + (EPS_START - EPS_END) * np.exp(-1.0 * episode / EPS_DECAY)
                if random.random() < eps_threshold:
                    masked_logits = masked_logits / 4

                # Check for NaNs in masked_logits
                if torch.isnan(masked_logits).any():
                    print(f"Episode {episode}, NaNs in masked_logits after masking.")
                    break

                # Compute probabilities
                probs = F.softmax(masked_logits, dim=0)

                # Check for NaNs in probs
                if torch.isnan(probs).any():
                    print(f"Episode {episode}, NaNs in probs after softmax.")
                    break

                try:
                    m = torch.distributions.Categorical(probs)
                    action_token = m.sample()
                    log_prob = m.log_prob(action_token)
                except ValueError as e:
                    print(f"Episode {episode}, error in sampling action: {e}")
                    break

            log_probs.append(log_prob)
            input_tokens.append(action_token.item())
            output_tokens.append(action_token.item())

            action = action_token.item()
            reward = 0.0
            if state == 'expect_action':
                if action == vocab['Comparison']:
                    state = 'expect_index1'
                elif action == vocab['Swap']:
                    if env.indices is None:
                        reward = INVALID_ACTION_REWARD
                        rewards.append(reward)
                        done = True
                        continue
                    action_tokens = [vocab['Swap']]
                    response_token, reward, done, current_list, _ = env.step(action_tokens)
                    steps += 1
                    if done and reward == SUCCESS_REWARD:
                        success = True
                        if episode % 100 == 0:
                            print(action_sequence_str)
                    if verbose:
                        print("Reward:", reward)
                    state = 'expect_action'
                else:
                    reward = INVALID_ACTION_REWARD
                    done = True
            elif state == 'expect_index1':
                index1_token = action_token
                state = 'expect_index2'
            elif state == 'expect_index2':
                index2_token = action_token
                action_tokens = [vocab['Comparison'], index1_token.item(), index2_token.item()]
                comparisons.append((int(inv_vocab[index1_token.item()]), 
                                    int(inv_vocab[index2_token.item()])))
                response_token, reward, done, current_list, additional_response_tokens = env.step(action_tokens)
                steps += 1
                if verbose:
                    print("Reward:", reward)
                if response_token is not None:
                    input_tokens.append(response_token)
                    output_tokens.append(response_token)
                    output_tokens.extend(additional_response_tokens)
                #
                if done and reward == SUCCESS_REWARD:
                    success = True
                    #if episode % 1 == 0:
                    #    print(1, decode(output_tokens, inv_vocab))
                else:
                    reward += COMPARISON_ENTROPY_MULTIPLIER * compute_min_delta_entropy(comparisons)
                #    
                state = 'expect_action'
            else:
                reward = INVALID_ACTION_REWARD
                done = True

            rewards.append(reward)
        #
        if success or len(output_tokens) >= MAX_STEPS // 3:
            action_sequence_str = decode(output_tokens, inv_vocab)
            f_training_data.write(action_sequence_str + (' success\n' if success else ' failure\n'))
            f_training_data.flush()
        # Post processing of each episode
        success_rewards = [0.0] * len(rewards)
        if success: 
            num_successes += 1
            success_rewards[-1] = SUCCESS_REWARD
            success_step_cnts.append(steps)
        #
        assert len(log_probs) == len(rewards), "log_probs and returns have different sizes!"

        if len(log_probs) == 0:
            continue  # Skip if no actions were taken

        # Compute returns and loss within autocast
        with torch.autocast(device_type=device.type, dtype=torch.bfloat16):
            # Compute returns
            returns1 = compute_bellman_returns(rewards, SHORTTERM_GAMMA)
            returns2 = compute_bellman_returns(success_rewards, LONGTERM_GAMMA)
            returns = torch.tensor(np.array(returns1) + np.array(returns2)).to(device)

            # Check for NaNs in returns
            if torch.isnan(returns).any():
                print(f"Episode {episode}, NaNs in returns.")
                continue

            # Compute loss
            loss = 0
            for log_prob, R in zip(log_probs, returns):
                loss -= log_prob * R

            # Check for NaNs in loss
            if torch.isnan(loss):
                print(f"Episode {episode}, NaN in loss.")
                continue

        optimizer.zero_grad()
        loss.backward()
        torch.nn.utils.clip_grad_norm_(model.parameters(), max_norm=1.0)  # Gradient clipping
        optimizer.step()

        episode_cnt += 1
        total_reward += sum(rewards)
        t2 = time.time()
        if episode % 1 == 0:
            print(f"Episode {episode}, loss:{loss.item():.4f}, {'succeed' if success else 'fail'}, steps:{steps}, total reward:{sum(rewards):.4f}, {t2-t1} sec")
            
        # Save checkpoint
        if episode > 0 and episode % EPISODES_SAVE == 0:
            avg_reward = total_reward / episode_cnt
            #assert len(success_step_cnts) == num_successes
            success_rate = num_successes / episode_cnt
            avg_steps = sum(success_step_cnts) / len(success_step_cnts)
            episode_cnt = 0
            total_reward = 0.0
            num_successes = 0
            total_steps = 0
            save_checkpoint(model, optimizer, episode, OUTPUT_DIR, f"ckpt_{episode}_{success_rate:.4f}_{avg_steps:.2f}.pth")
            #
            # Reduce the lr
            scheduler.step()
            # Optionally, log the learning rate
            current_lr = scheduler.get_last_lr()[0]
            print(f"Learning rate = {current_lr:.6f}")

if __name__ == "__main__":
    for i in range(100):
        train(verbose=False)


/home/mcwave/.local/lib/python3.10/site-packages/torch/nn/modules/transformer.py:282: UserWarning: enable_nested_tensor is True, but self.use_nested_tensor is False because encoder_layer.self_attn.batch_first was not True(use batch_first for better inference performance)
  warnings.warn(f"enable_nested_tensor is True, but self.use_nested_tensor is False because {why_not_sparsity_fast_path}")


Episode 0, loss:-7.1855, fail, steps:0, total reward:-10.0000, 0.3116276264190674 sec
Episode 1, loss:-50.4666, fail, steps:7, total reward:-11.5000, 0.06577587127685547 sec
Episode 2, loss:-7.2545, fail, steps:0, total reward:-10.0000, 0.004176139831542969 sec
Episode 3, loss:-48.3130, fail, steps:6, total reward:-10.5000, 0.04178667068481445 sec
Episode 4, loss:-42.6380, fail, steps:4, total reward:-11.9000, 0.028123140335083008 sec
Episode 5, loss:-73.6094, fail, steps:23, total reward:-14.3000, 0.3475956916809082 sec
Episode 6, loss:-72.6561, fail, steps:16, total reward:-14.2000, 0.11855435371398926 sec
Episode 7, loss:-8.4544, fail, steps:0, total reward:-10.0000, 0.00569915771484375 sec
Episode 8, loss:-90.3037, fail, steps:51, total reward:-18.2000, 0.4095771312713623 sec
Episode 9, loss:-21.5796, fail, steps:0, total reward:-10.0000, 0.011140584945678711 sec
Episode 10, loss:-96.8953, fail, steps:36, total reward:-18.2000, 0.27448558807373047 sec
Episode 11, loss:-90.5488, fai

Episode 92, loss:-210.3371, fail, steps:170, total reward:-38.8000, 1.5288634300231934 sec
Episode 93, loss:-211.7484, fail, steps:174, total reward:-37.5000, 1.6646676063537598 sec
Episode 94, loss:-219.2794, fail, steps:169, total reward:-41.1000, 1.6575183868408203 sec
Episode 95, loss:-172.2401, fail, steps:146, total reward:-29.2000, 1.4555978775024414 sec
Episode 96, loss:-171.8502, fail, steps:177, total reward:-29.2000, 1.9280083179473877 sec
Episode 97, loss:-140.3324, fail, steps:67, total reward:-23.8000, 0.6459338665008545 sec
Episode 98, loss:-182.3960, fail, steps:174, total reward:-31.5000, 1.662843942642212 sec
Episode 99, loss:-69.9569, fail, steps:25, total reward:-12.3000, 0.262789249420166 sec
Episode 100, loss:-73.7042, fail, steps:34, total reward:-12.4000, 0.26843738555908203 sec
Episode 101, loss:-146.3105, fail, steps:176, total reward:-24.2000, 1.5674946308135986 sec
Episode 102, loss:-182.4652, fail, steps:177, total reward:-32.1000, 1.6990666389465332 sec
Ep

Episode 183, loss:-165.1622, fail, steps:176, total reward:-24.2000, 1.722926378250122 sec
Episode 184, loss:-128.8905, fail, steps:182, total reward:-15.6000, 1.7491474151611328 sec
Episode 185, loss:-132.7003, fail, steps:187, total reward:-14.0000, 1.7557837963104248 sec
Episode 186, loss:-111.9393, fail, steps:189, total reward:-10.0000, 1.8217568397521973 sec
Episode 187, loss:-74.9496, fail, steps:13, total reward:-11.3000, 0.18546056747436523 sec
Episode 188, loss:-47.8890, fail, steps:2, total reward:-9.3000, 0.022938966751098633 sec
Episode 189, loss:-176.0698, fail, steps:179, total reward:-23.9000, 1.554006814956665 sec
Episode 190, loss:-120.1144, fail, steps:191, total reward:-8.7000, 1.6861209869384766 sec
Episode 191, loss:-123.0746, fail, steps:190, total reward:-11.0000, 1.750762939453125 sec
Episode 192, loss:-141.6378, fail, steps:182, total reward:-17.6000, 1.778843879699707 sec
Episode 193, loss:-59.0052, fail, steps:6, total reward:-9.2000, 0.11470675468444824 sec

Episode 275, loss:-46.9875, succeed, steps:163, total reward:-10.5000, 1.357170581817627 sec
Episode 276, loss:-121.4653, fail, steps:187, total reward:-11.3000, 1.783097743988037 sec
Episode 277, loss:-127.0908, fail, steps:187, total reward:-14.0000, 1.7360658645629883 sec
Episode 278, loss:-138.8654, fail, steps:182, total reward:-17.6000, 1.824378252029419 sec
Episode 279, loss:-148.8065, fail, steps:179, total reward:-21.9000, 1.7716069221496582 sec
Episode 280, loss:-117.7024, fail, steps:184, total reward:-13.6000, 1.770432949066162 sec
Episode 281, loss:-67.7877, fail, steps:29, total reward:-8.3000, 0.29839587211608887 sec
Episode 282, loss:-153.3885, fail, steps:184, total reward:-19.6000, 1.5871341228485107 sec
Episode 283, loss:-164.0713, fail, steps:177, total reward:-25.2000, 1.739924430847168 sec
Episode 284, loss:-75.4084, fail, steps:195, total reward:0.6000, 1.778954267501831 sec
Episode 285, loss:-110.9092, fail, steps:106, total reward:-11.9000, 0.9709696769714355 s

...

Episode 2730, loss:-35.0357, fail, steps:195, total reward:2.6000, 1.9390504360198975 sec
Episode 2731, loss:-62.4679, fail, steps:192, total reward:-3.7000, 1.9104821681976318 sec
Episode 2732, loss:-38.9686, fail, steps:196, total reward:3.6000, 1.8744664192199707 sec
Episode 2733, loss:-17.2490, fail, steps:202, total reward:12.2000, 1.9271571636199951 sec
Episode 2734, loss:-31.1339, fail, steps:196, total reward:4.9000, 1.9138798713684082 sec
Episode 2735, loss:-35.1205, fail, steps:194, total reward:1.6000, 1.9778549671173096 sec
Episode 2736, loss:-35.6838, fail, steps:198, total reward:4.9000, 2.005119800567627 sec
Episode 2737, loss:-24.6214, fail, steps:198, total reward:6.9000, 1.9453237056732178 sec
Episode 2738, loss:-67.0359, fail, steps:106, total reward:-1.5000, 0.9704735279083252 sec
Episode 2739, loss:-47.4257, fail, steps:194, total reward:1.6000, 1.7884061336517334 sec
Episode 2740, loss:-41.7366, fail, steps:196, total reward:3.6000, 1.8280515670776367 sec
Episode 

Episode 2821, loss:-66.8502, fail, steps:73, total reward:-2.0000, 0.6635544300079346 sec
Episode 2822, loss:-53.3738, fail, steps:193, total reward:-0.7000, 1.685086727142334 sec
Episode 2823, loss:-47.7438, fail, steps:192, total reward:-1.7000, 1.8163659572601318 sec
Episode 2824, loss:-49.4678, fail, steps:192, total reward:-1.7000, 1.873204231262207 sec
Episode 2825, loss:-51.1689, fail, steps:190, total reward:-3.7000, 1.846299648284912 sec
Episode 2826, loss:-54.3917, fail, steps:191, total reward:-2.7000, 1.8973066806793213 sec
Episode 2827, loss:-36.8806, fail, steps:196, total reward:3.6000, 1.9487006664276123 sec
Episode 2828, loss:-29.1747, fail, steps:199, total reward:9.2000, 1.9213106632232666 sec
Episode 2829, loss:-68.1789, fail, steps:187, total reward:-8.0000, 1.9270083904266357 sec
Episode 2830, loss:-34.9138, fail, steps:196, total reward:3.6000, 1.9342949390411377 sec
Episode 2831, loss:-59.4630, fail, steps:193, total reward:-0.7000, 1.9521777629852295 sec
Episod

Episode 2912, loss:-10.6340, fail, steps:205, total reward:17.8000, 1.9618780612945557 sec
Episode 2913, loss:-38.1942, fail, steps:195, total reward:2.6000, 1.933075189590454 sec
Episode 2914, loss:-60.5180, fail, steps:190, total reward:-3.7000, 1.9055187702178955 sec
Episode 2915, loss:-76.3465, fail, steps:185, total reward:-11.3000, 2.035398244857788 sec
Episode 2916, loss:-55.5052, fail, steps:190, total reward:-3.7000, 1.858872413635254 sec
Episode 2917, loss:4.5253, fail, steps:207, total reward:19.8000, 1.9121134281158447 sec
Episode 2918, loss:-6.9272, fail, steps:205, total reward:16.5000, 1.892221450805664 sec
Episode 2919, loss:-15.3606, fail, steps:202, total reward:13.5000, 1.9988274574279785 sec
Episode 2920, loss:-35.4636, fail, steps:198, total reward:6.9000, 1.934737205505371 sec
Episode 2921, loss:-65.5178, fail, steps:189, total reward:-6.0000, 2.015781879425049 sec
Episode 2922, loss:-57.9170, fail, steps:188, total reward:-7.0000, 1.92570161819458 sec
Episode 292

Episode 3001, loss:-68.6922, fail, steps:188, total reward:-7.0000, 1.922302484512329 sec
Episode 3002, loss:-19.1713, fail, steps:200, total reward:10.2000, 1.9206938743591309 sec
Episode 3003, loss:-26.7831, fail, steps:199, total reward:7.9000, 1.9304423332214355 sec
Episode 3004, loss:-62.1772, fail, steps:190, total reward:-3.7000, 2.0081708431243896 sec
Episode 3005, loss:-59.1180, fail, steps:190, total reward:-5.0000, 2.025451898574829 sec
Episode 3006, loss:-54.6004, fail, steps:191, total reward:-2.7000, 1.9423930644989014 sec
Episode 3007, loss:-60.7689, fail, steps:190, total reward:-3.7000, 1.9524376392364502 sec
Episode 3008, loss:-50.6754, fail, steps:190, total reward:-3.7000, 1.9668431282043457 sec
Episode 3009, loss:33.8763, succeed, steps:188, total reward:12.0000, 1.8260459899902344 sec
Episode 3010, loss:-47.5021, fail, steps:196, total reward:4.9000, 1.9942808151245117 sec
Episode 3011, loss:-23.3883, fail, steps:200, total reward:10.2000, 1.9380991458892822 sec
E

Episode 3092, loss:-44.4778, fail, steps:193, total reward:0.6000, 1.9417626857757568 sec
Episode 3093, loss:-129.5026, fail, steps:180, total reward:-18.5000, 1.86952543258667 sec
Episode 3094, loss:-59.3341, fail, steps:189, total reward:-6.0000, 1.9850690364837646 sec
Episode 3095, loss:9.2895, fail, steps:206, total reward:18.8000, 2.0443685054779053 sec
Episode 3096, loss:-68.5861, fail, steps:190, total reward:-5.7000, 1.9618287086486816 sec
Episode 3097, loss:-8.6289, fail, steps:203, total reward:14.5000, 1.960768699645996 sec
Episode 3098, loss:-36.8955, fail, steps:195, total reward:2.6000, 1.8637006282806396 sec
Episode 3099, loss:-79.1106, fail, steps:185, total reward:-11.3000, 1.9978933334350586 sec
Episode 3100, loss:-53.2640, fail, steps:192, total reward:-1.7000, 1.9732913970947266 sec
Episode 3101, loss:-75.4462, fail, steps:32, total reward:-7.9000, 0.3574678897857666 sec
Episode 3102, loss:-61.9431, fail, steps:188, total reward:-7.0000, 1.7037127017974854 sec
Episo